# w

In [1]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from sklearn.decomposition import PCA
# umap
from umap import UMAP

In [6]:
# mnist 
from sklearn.datasets import fetch_openml

data = fetch_openml('mnist_784', version=1, as_frame=False)
X = data.data
y = data.target.astype(int)
num = 1000

dataset_mnist = {
    "X": X[:num],
    "y": y[:num]
}

c:\Users\acero\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\datasets\_openml.py:1022: FutureWarning: The default value of `parser` will change from `'liac-arff'` to `'auto'` in 1.4. You can set `parser='auto'` to silence this warning. Therefore, an `ImportError` will be raised from 1.4 if the dataset is dense and pandas is not installed. Note that the pandas parser may return different data types. See the Notes Section in fetch_openml's API doc for details.
  warn(


In [68]:
# sample plot by pca

def sample_plot_pca(dataset, n_components=2):
    pca = PCA(n_components=n_components)
    X_transformed = pca.fit_transform(dataset["X"])

    #  categorical colors
    dataset["y"] = dataset["y"].astype(str)
    
    fig = px.scatter(
        x=X_transformed[:, 0],
        y=X_transformed[:, 1],
        color=dataset["y"],

    )
    fig.update_layout(
        width=800,
        height=800)
    fig.show()

def sample_plot_umap(dataset, n_components=2, label=True):
    umap = UMAP(n_components=n_components)
    X_transformed = umap.fit_transform(dataset["X"])

    #  categorical colors
    if label:
        colors = dataset["y"].astype(str)
    else:
        colors = np.zeros(len(dataset["X"]))
    
    fig = px.scatter(
        x=X_transformed[:, 0],
        y=X_transformed[:, 1],
        color=colors,)
    fig.update_layout(
        width=800,
        height=800)
    fig.show()

In [12]:
sample_plot_pca(dataset_mnist, n_components=2)

In [ ]:
# work vec dataset 
# gensim
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from gensim.models import Word2Vec


# または
sentences = 
model = Word2Vec(sentences, vector_size=100, window=5, min_count=1, workers=4)

# 単語とベクトルを取得
words = list(model.wv.index_to_key)  # モデル内の単語リスト
vectors = [model.wv[word] for word in words]


# dict形式にまとめる
dataset_w2v = {"X": words, "y": vectors}

sample_plot_pca(dataset_w2v, n_components=2)




In [16]:
# 大きさ
dataset_w2v["X"].shape

(7, 2)

In [59]:
# glove
import os
file_path = "../../../data/multidimensional-data/glove/processed"
print(f"pwd{os.getcwd()}")
import numpy as np
import pandas as pd
X = np.load(os.path.join(file_path, "data.npy"))
y = pd.read_csv(os.path.join(file_path, "metadata.csv"), header=None)
print(X.shape, len(y))
dataset_glove = {"X": X, "y": np.array(y[0].values)}


pwdc:\Users\acero\Work_Research\DRZoom\src\experiments\12_select_axes_pca
(10000, 300) 10000


In [66]:
plot_cumulative_variance(dataset_glove)
plot_scatter_matrix(dataset_glove, n_components=10, label=False)

In [69]:
sample_plot_umap(dataset_glove, n_components=2, label=False)

In [70]:
# fashion mnist
from sklearn.datasets import fetch_openml
data = fetch_openml('Fashion-MNIST', version=1, as_frame=False)
X = data.data
y = data.target.astype(int)
num = 1000
dataset_fashion_mnist = {
    "X": X[:num],
    "y": y[:num]
}

c:\Users\acero\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\datasets\_openml.py:1022: FutureWarning:

The default value of `parser` will change from `'liac-arff'` to `'auto'` in 1.4. You can set `parser='auto'` to silence this warning. Therefore, an `ImportError` will be raised from 1.4 if the dataset is dense and pandas is not installed. Note that the pandas parser may return different data types. See the Notes Section in fetch_openml's API doc for details.



In [71]:
plot_cumulative_variance(dataset_mnist)
plot_scatter_matrix(dataset_mnist, n_components=10)

# 複数の主成分軸の取得と選択

In [ ]:
# 累積分散のプロット
def plot_cumulative_variance(dataset):
    pca = PCA()
    pca.fit(dataset["X"])
    cumulative_variance = np.cumsum(pca.explained_variance_ratio_)
    fig = px.line(
        x=np.arange(1, len(cumulative_variance) + 1),
        y=cumulative_variance)
    fig.show()
# 10の主成分の2つの組み合わせ: scatter matrix
def plot_scatter_matrix(dataset, n_components=10, label=True):
    pca = PCA(n_components=n_components)
    X_transformed = pca.fit_transform(dataset["X"])

    if label:
        colors = dataset["y"].astype(int)
    else:
        # all 1
        colors = np.ones(len(dataset["y"]))
    


    fig = go.Figure(data=go.Splom(
        dimensions=[dict(label=f'PC{i+1}', values=X_transformed[:, i])
                    for i in range(n_components)],
        text=dataset["y"],
        marker=dict(color=colors,
                    showscale=False,  # colors encode categorical variables
                    line_color='white', line_width=0.5,
                    size=2)
    ))
    fig.update_layout(
        title=dict(text='PCA Scatter Matrix'),
        dragmode='select',
        width=800,
        height=800,
        hovermode='closest',
    )
    fig.show()



    

# metric

In [141]:
from sklearn.neighbors import NearestNeighbors
# missing neighbors


def trustworthiness(data, mapping, k=7):
    n = data.shape[0]
    # 高次元と低次元の近傍インデックスを取得
    data_neighbors = NearestNeighbors(n_neighbors=n-1).fit(data).kneighbors(return_distance=False)
    mapping_neighbors = NearestNeighbors(n_neighbors=k+1).fit(mapping).kneighbors(return_distance=False)

    total = 0
    for i in range(n):
        ranks = {j: rank for rank, j in enumerate(data_neighbors[i])}
        for j in mapping_neighbors[i][1:]:  # 除く: 自分自身
            if j not in data_neighbors[i][:k+1]:
                total += ranks[j] - k

    normalizer = n * k * (2*n - 3*k - 1) / 2
    T = 1 - total / normalizer
    print(f"Trustworthiness: {T:.4f}")
    return T


def continuity(data, mapping, k=7):
    n = data.shape[0]
    data_neighbors = NearestNeighbors(n_neighbors=k+1).fit(data).kneighbors(return_distance=False)
    mapping_neighbors = NearestNeighbors(n_neighbors=n-1).fit(mapping).kneighbors(return_distance=False)

    total = 0
    for i in range(n):
        ranks = {j: rank for rank, j in enumerate(mapping_neighbors[i])}
        for j in data_neighbors[i][1:]:
            if j not in mapping_neighbors[i][:k+1]:
                total += ranks[j] - k

    normalizer = n * k * (2*n - 3*k - 1) / 2
    C = 1 - total / normalizer
    print(f"Continuity: {C:.4f}")
    return C


In [138]:
pca = PCA(n_components=2)
pca_result = pca.fit_transform(dataset_glove["X"])
trustworthiness(dataset_glove["X"], pca_result, k=7)


Trustworthiness: 0.6499


0.6498937030733807

In [142]:
continuity(dataset_glove["X"], pca_result, k=7)

Continuity: 0.8778


0.8777761880926161

In [143]:
umap = UMAP(n_components=2)
umap_result = umap.fit_transform(dataset_glove["X"])
trustworthiness(dataset_glove["X"], umap_result, k=7)
continuity(dataset_glove["X"], umap_result, k=7)

Trustworthiness: 0.8346
Continuity: 0.9186


0.9185589577106246

In [159]:
def evaluate_pca(dataset, n_components=2):
    pca = PCA(n_components=n_components)
    pca_result = pca.fit_transform(dataset["X"])

    continuity(dataset["X"], pca_result, k=7)
    trustworthiness(dataset["X"], pca_result, k=7)

def evaluate_umap(dataset, n_components=2):
    umap = UMAP(n_components=n_components)
    umap_result = umap.fit_transform(dataset["X"])

    continuity(dataset["X"], umap_result, k=7)
    trustworthiness(dataset["X"], umap_result, k=7)

evaluate_pca(dataset_mnist)
evaluate_umap(dataset_mnist)

Continuity: 0.9030
Trustworthiness: 0.7473
Continuity: 0.9596
Trustworthiness: 0.9613


In [183]:
def continuity_by_label(data, mapping, y, label=0, k=7):
    n = data.shape[0]
    data_neighbors = NearestNeighbors(n_neighbors=k+1).fit(data).kneighbors(return_distance=False)
    mapping_neighbors = NearestNeighbors(n_neighbors=n-1).fit(mapping).kneighbors(return_distance=False)

    total = 0
    n_label = np.sum(y == label)
    for i in range(n):
        if y[i] != label:
            continue
        ranks = {j: rank for rank, j in enumerate(mapping_neighbors[i])}
        for j in data_neighbors[i][1:]:
            if j not in mapping_neighbors[i][:k+1]:
                total += ranks[j] - k
    normalizer = n_label * k * (2 * n_label - 3 * k - 1) / 2
    C = 1 - total / normalizer
    print(f"Continuity for label {label}: {C:.4f}")
    return C


def trustworthiness_by_label(data, mapping, y, label=0, k=7):
    n = data.shape[0]
    data_neighbors = NearestNeighbors(n_neighbors=n-1).fit(data).kneighbors(return_distance=False)
    mapping_neighbors = NearestNeighbors(n_neighbors=k+1).fit(mapping).kneighbors(return_distance=False)

    total = 0
    n_label = np.sum(y == label)
    for i in range(n):
        if y[i] != label:
            continue
        ranks = {j: rank for rank, j in enumerate(data_neighbors[i])}
        for j in mapping_neighbors[i][1:]:  # 除く: 自分自身
            if j not in data_neighbors[i][:k+1]:
                total += ranks[j] - k

    normalizer = n_label * k * (2 * n_label - 3 * k - 1) / 2
    T = 1 - total / normalizer
    print(f"Trustworthiness for label {label}: {T:.4f}")
    return T

In [187]:
umap_result = umap.fit_transform(dataset_mnist["X"])
continuity(dataset_mnist["X"], umap_result, k=7)
trustworthiness(dataset_mnist["X"], umap_result, k=7)
continuities = [ continuity_by_label(dataset_mnist["X"], umap_result, dataset_mnist["y"], label=label, k=7) for label in np.unique(dataset_mnist["y"]) ]
trustworthies = [ trustworthiness_by_label(dataset_mnist["X"], umap_result, dataset_mnist["y"], label=label, k=7) for label in np.unique(dataset_mnist["y"]) ]
fig = px.bar(y=trustworthies, x=np.unique(dataset_mnist["y"]), labels={'x': 'Label', 'y': 'Trustworthiness'}).show()
fig = px.bar(y=continuities, x=np.unique(dataset_mnist["y"]), labels={'x': 'Label', 'y': 'Continuity'}).show()
fig = px.scatter(x=umap_result[:, 0], y=umap_result[:, 1], color=dataset_mnist["y"].astype(str), title="UMAP Result for MNIST").show()

Continuity: 0.9581
Trustworthiness: 0.9633
Continuity for label 0: 0.7897
Continuity for label 1: 0.9106
Continuity for label 2: -0.1013
Continuity for label 3: 0.3616
Continuity for label 4: 0.6279
Continuity for label 5: 0.1557
Continuity for label 6: 0.5888
Continuity for label 7: 0.7169
Continuity for label 8: 0.3470
Continuity for label 9: 0.6431
Trustworthiness for label 0: 0.8371
Trustworthiness for label 1: 0.8172
Trustworthiness for label 2: 0.2302
Trustworthiness for label 3: 0.4251
Trustworthiness for label 4: 0.5867
Trustworthiness for label 5: 0.3655
Trustworthiness for label 6: 0.7303
Trustworthiness for label 7: 0.6919
Trustworthiness for label 8: 0.4065
Trustworthiness for label 9: 0.6634


In [184]:
pca_result = pca.fit_transform(dataset_mnist["X"])
for label in np.unique(dataset_mnist["y"]):
    print(f"Label: {label}")
    continuity_by_label(dataset_mnist["X"], pca_result, dataset_mnist["y"], label=label, k=7)
for label in np.unique(dataset_mnist["y"]):
    print(f"Label: {label}")
    trustworthiness_by_label(dataset_mnist["X"], pca_result, dataset_mnist["y"], label=label, k=7)


Label: 0
Continuity for label 0: -0.0559
Label: 1
Continuity for label 1: 0.7316
Label: 2
Continuity for label 2: -0.5681
Label: 3
Continuity for label 3: -0.2883
Label: 4
Continuity for label 4: -0.0042
Label: 5
Continuity for label 5: -0.5728
Label: 6
Continuity for label 6: -0.3433
Label: 7
Continuity for label 7: 0.2053
Label: 8
Continuity for label 8: -0.4721
Label: 9
Continuity for label 9: 0.0277
Label: 0
Trustworthiness for label 0: -1.8535
Label: 1
Trustworthiness for label 1: 0.3988
Label: 2
Trustworthiness for label 2: -2.7120
Label: 3
Trustworthiness for label 3: -2.4124
Label: 4
Trustworthiness for label 4: -1.4015
Label: 5
Trustworthiness for label 5: -3.9628
Label: 6
Trustworthiness for label 6: -3.1918
Label: 7
Trustworthiness for label 7: -0.6653
Label: 8
Trustworthiness for label 8: -2.8703
Label: 9
Trustworthiness for label 9: -1.3383


In [181]:
fig = px.scatter(
    x=pca_result[:, 0],
    y=pca_result[:, 1],
    color=dataset_mnist["y"].astype(str),
    title="PCA Result for MNIST"
).show()

In [190]:
import dash
from dash import Dash, dcc, html, Input, Output
import plotly.express as px
import numpy as np
from sklearn.manifold import TSNE
import base64

# --- MNIST前提 ---
# dataset["X"]: (n_samples, 784)
# dataset["y"]: (n_samples, )
# ↓ 例として読み込みたい人向けサンプル（コメント外すと動作）
# from sklearn.datasets import load_digits
# digits = load_digits()
# dataset = {"X": digits.data, "y": digits.target}
dataset = dataset_mnist  # ここではMNISTデータセットを使用

# --- t-SNEで埋め込み ---
embedding = UMAP(n_components=2, random_state=42).fit_transform(dataset["X"])

# --- 画像をbase64でエンコードする関数 ---
def image_to_base64(image_array):
    import io
    from PIL import Image
    image = Image.fromarray(np.uint8(image_array * 255))  # 0〜1に正規化されていれば調整
    buffered = io.BytesIO()
    image = image.resize((140, 140))  # 拡大表示
    image.save(buffered, format="PNG")
    encoded = base64.b64encode(buffered.getvalue()).decode()
    return f"data:image/png;base64,{encoded}"

# --- scatter plotのdata frame化 ---
import pandas as pd
df = pd.DataFrame({
    'x': embedding[:, 0],
    'y': embedding[:, 1],
    'label': dataset["y"],
    'index': np.arange(len(dataset["y"]))
})

# --- Dashアプリ構築 ---
app = Dash(__name__)

app.layout = html.Div([
    html.H3("MNIST t-SNE Visualization"),
    dcc.Graph(
        id='scatter-plot',
        figure=px.scatter(
            df, x='x', y='y', color=df['label'].astype(str),
            hover_data=['label', 'index'],
            title="Click a point to view the image"
        )
    ),
    html.Div(id='image-container', style={'textAlign': 'center', 'marginTop': '30px'})
])

# --- コールバック：点クリックで画像表示 ---
@app.callback(
    Output('image-container', 'children'),
    Input('scatter-plot', 'clickData')
)
def display_image(clickData):
    if clickData is None:
        return html.P("Click on a point to see the image.")

    idx = clickData['points'][0]['customdata'][1]  # 'index'に対応
    image = dataset["X"][idx].reshape(28, 28)

    # 正規化（必要なら）
    if image.max() > 1.0:
        image = image / 255.0

    encoded_image = image_to_base64(image)
    return html.Img(src=encoded_image)

# --- 実行（Jupyter以外ではこのまま） ---
if __name__ == '__main__':
    app.run_server(debug=True)


c:\Users\acero\AppData\Local\Programs\Python\Python311\Lib\site-packages\umap\umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.



In [195]:
# text embedding

import dash
from dash import Dash, dcc, html, Input, Output
import plotly.express as px
import numpy as np
from sklearn.manifold import TSNE
import pandas as pd

# ---------------------------
# ✅ 前提データ
# embeddings: (n_words, dim)
# words: list of strings
# ---------------------------

# サンプル作りたい場合（以下コメント外すとランダム埋め込みを生成）
# words = ["apple", "banana", "car", "train", "dog", "cat", "sun", "moon", "king", "queen"]
# embeddings = np.random.randn(len(words), 50)

# --- t-SNEで2次元に次元圧縮 ---
dataset = dataset_glove
embedding_2d = UMAP(n_components=2, random_state=42).fit_transform(dataset["X"])

# --- plot用DataFrame作成 ---
df = pd.DataFrame({
    'x': embedding_2d[:, 0],
    'y': embedding_2d[:, 1],
    'word': dataset["y"]
})
fig = px.scatter(df, x='x', y='y', hover_name='word',
                          title="Click a point to see the word")
fig.update_traces(marker=dict(size=2))

# --- Dash App構築 ---
app = Dash(__name__)

app.layout = html.Div([
    html.H3("Text Embedding Visualization"),
    dcc.Graph(
        id='scatter-plot',
        figure=fig
    ),
    html.Div(id='word-display', style={'textAlign': 'center', 'fontSize': 24, 'marginTop': '30px'})
])

# --- コールバック：クリックで単語表示 ---
@app.callback(
    Output('word-display', 'children'),
    Input('scatter-plot', 'clickData')
)
def display_word(clickData):
    if clickData is None:
        return "Click on a point to see the word."
    word = clickData['points'][0]['hovertext']
    return f"You clicked: {word}"

# --- 実行 ---
if __name__ == '__main__':
    app.run_server(debug=True)


c:\Users\acero\AppData\Local\Programs\Python\Python311\Lib\site-packages\umap\umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.

